# chunker: default program

In [2]:
from chunker import *
import os

In [3]:
import torch.nn as nn
import torch.nn.functional as F
torch.manual_seed(1)

## Test

In [3]:
import gzip

In [24]:
def read_conll(handle, input_idx=0, label_idx=2):
    conll_data = []
    contents = re.sub(r'\n\s*\n', r'\n\n', handle.read())
    contents = contents.rstrip()
    for sent_string in contents.split('\n\n'):
        annotations = list(zip(*[word_string.split() for word_string in sent_string.split('\n') ]))
        assert(input_idx < len(annotations))
        if label_idx < 0:
            conll_data.append( annotations[input_idx] )
            logging.info("CoNLL: {}".format( " ".join(annotations[input_idx])))
        else:
            assert(label_idx < len(annotations))
            conll_data.append(( annotations[input_idx], annotations[label_idx] ))
            logging.info("CoNLL: {} ||| {}".format( " ".join(annotations[input_idx]), " ".join(annotations[label_idx])))
    return conll_data

In [20]:
with gzip.open(os.path.join('../data', 'train.txt.gz'), 'rt') as f:
    training_data = read_conll(f)
    # sent_string read in evey line in train.txt

[UNK] NN B-NP
in IN B-PP
the DT B-NP
pound NN I-NP
is VBZ B-VP
widely RB I-VP
expected VBN I-VP
to TO I-VP
take VB I-VP
another DT B-NP
sharp JJ I-NP
dive NN I-NP
if IN B-SBAR
trade NN B-NP
figures NNS I-NP
for IN B-PP
September NNP B-NP
, , O
due JJ B-ADJP
for IN B-PP
release NN B-NP
tomorrow NN B-NP
, , O
fail VB B-VP
to TO I-VP
show VB I-VP
a DT B-NP
substantial JJ I-NP
improvement NN I-NP
from IN B-PP
July NNP B-NP
and CC I-NP
August NNP I-NP
's POS B-NP
near-record JJ I-NP
[UNK] NNS I-NP
. . O
Chancellor NNP O
of IN B-PP
the DT B-NP
Exchequer NNP I-NP
Nigel NNP B-NP
Lawson NNP I-NP
's POS B-NP
restated VBN I-NP
commitment NN I-NP
to TO B-PP
a DT B-NP
firm NN I-NP
monetary JJ I-NP
policy NN I-NP
has VBZ B-VP
helped VBN I-VP
to TO I-VP
prevent VB I-VP
a DT B-NP
[UNK] NN I-NP
in IN B-PP
sterling NN B-NP
over IN B-PP
the DT B-NP
past JJ I-NP
week NN I-NP
. . O
But CC O
analysts NNS B-NP
[UNK] VBP B-VP
underlying VBG B-NP
support NN I-NP
for IN B-PP
sterling NN B-NP
has VBZ B-VP
been V

`` `` O
But CC O
one CD B-NP
gets VBZ B-VP
fed VBN I-VP
up IN B-PRT
with IN B-PP
importing VBG B-VP
information NN B-NP
and CC I-NP
news NN I-NP
. . O
'' '' O
Mr. NNP B-NP
Shioya NNP I-NP
has VBZ B-VP
turned VBN I-VP
the DT B-NP
tables NNS I-NP
. . O
Today NN B-NP
, , O
he PRP B-NP
is VBZ B-VP
publisher NN B-NP
of IN B-PP
Business NNP B-NP
Tokyo NNP I-NP
magazine NN I-NP
, , O
the DT B-NP
first JJ I-NP
English-language JJ I-NP
business NN I-NP
magazine NN I-NP
[UNK] VBN B-VP
to TO B-PP
coverage NN B-NP
of IN B-PP
Japanese JJ B-NP
business NN I-NP
. . O
After IN B-PP
a DT B-NP
slick JJ I-NP
[UNK] NN I-NP
, , O
the DT B-NP
[UNK] JJ I-NP
magazine NN I-NP
has VBZ B-VP
been VBN I-VP
[UNK] VBN I-VP
this DT B-NP
month NN I-NP
by IN B-PP
its PRP$ B-NP
parent NN I-NP
company NN I-NP
, , O
Keizaikai NNP B-NP
Corp. NNP I-NP
, , O
the DT B-NP
Tokyo-based JJ I-NP
company NN I-NP
with IN B-PP
interests NNS B-NP
that WDT B-NP
include VBP B-VP
financial JJ B-NP
services NNS I-NP
, , O
book NN B-NP
pub

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [18]:
with gzip.open(os.path.join('../data', 'train.txt.gz'), 'rt') as f:
    training_data = read_conll(f)
    # annotations

[('[UNK]', 'in', 'the', 'pound', 'is', 'widely', 'expected', 'to', 'take', 'another', 'sharp', 'dive', 'if', 'trade', 'figures', 'for', 'September', ',', 'due', 'for', 'release', 'tomorrow', ',', 'fail', 'to', 'show', 'a', 'substantial', 'improvement', 'from', 'July', 'and', 'August', "'s", 'near-record', '[UNK]', '.'), ('NN', 'IN', 'DT', 'NN', 'VBZ', 'RB', 'VBN', 'TO', 'VB', 'DT', 'JJ', 'NN', 'IN', 'NN', 'NNS', 'IN', 'NNP', ',', 'JJ', 'IN', 'NN', 'NN', ',', 'VB', 'TO', 'VB', 'DT', 'JJ', 'NN', 'IN', 'NNP', 'CC', 'NNP', 'POS', 'JJ', 'NNS', '.'), ('B-NP', 'B-PP', 'B-NP', 'I-NP', 'B-VP', 'I-VP', 'I-VP', 'I-VP', 'I-VP', 'B-NP', 'I-NP', 'I-NP', 'B-SBAR', 'B-NP', 'I-NP', 'B-PP', 'B-NP', 'O', 'B-ADJP', 'B-PP', 'B-NP', 'B-NP', 'O', 'B-VP', 'I-VP', 'I-VP', 'B-NP', 'I-NP', 'I-NP', 'B-PP', 'B-NP', 'I-NP', 'I-NP', 'B-NP', 'I-NP', 'I-NP', 'O')]
[('Chancellor', 'of', 'the', 'Exchequer', 'Nigel', 'Lawson', "'s", 'restated', 'commitment', 'to', 'a', 'firm', 'monetary', 'policy', 'has', 'helped', 'to',

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [25]:
with gzip.open(os.path.join('../data', 'train.txt.gz'), 'rt') as f:
    training_data = read_conll(f)
    print(training_data)

(('[UNK]', 'in', 'the', 'pound', 'is', 'widely', 'expected', 'to', 'take', 'another', 'sharp', 'dive', 'if', 'trade', 'figures', 'for', 'September', ',', 'due', 'for', 'release', 'tomorrow', ',', 'fail', 'to', 'show', 'a', 'substantial', 'improvement', 'from', 'July', 'and', 'August', "'s", 'near-record', '[UNK]', '.'), ('B-NP', 'B-PP', 'B-NP', 'I-NP', 'B-VP', 'I-VP', 'I-VP', 'I-VP', 'I-VP', 'B-NP', 'I-NP', 'I-NP', 'B-SBAR', 'B-NP', 'I-NP', 'B-PP', 'B-NP', 'O', 'B-ADJP', 'B-PP', 'B-NP', 'B-NP', 'O', 'B-VP', 'I-VP', 'I-VP', 'B-NP', 'I-NP', 'I-NP', 'B-PP', 'B-NP', 'I-NP', 'I-NP', 'B-NP', 'I-NP', 'I-NP', 'O'))


In [3]:
chunker = LSTMTagger(os.path.join('../data', 'train.txt.gz'), os.path.join('../data', 'chunker'), '.tar')
print(chunker.word_to_ix)

{'[UNK]': 0, 'in': 1, 'the': 2, 'pound': 3, 'is': 4, 'widely': 5, 'expected': 6, 'to': 7, 'take': 8, 'another': 9, 'sharp': 10, 'dive': 11, 'if': 12, 'trade': 13, 'figures': 14, 'for': 15, 'September': 16, ',': 17, 'due': 18, 'release': 19, 'tomorrow': 20, 'fail': 21, 'show': 22, 'a': 23, 'substantial': 24, 'improvement': 25, 'from': 26, 'July': 27, 'and': 28, 'August': 29, "'s": 30, 'near-record': 31, '.': 32, 'Chancellor': 33, 'of': 34, 'Exchequer': 35, 'Nigel': 36, 'Lawson': 37, 'restated': 38, 'commitment': 39, 'firm': 40, 'monetary': 41, 'policy': 42, 'has': 43, 'helped': 44, 'prevent': 45, 'sterling': 46, 'over': 47, 'past': 48, 'week': 49, 'But': 50, 'analysts': 51, 'underlying': 52, 'support': 53, 'been': 54, 'eroded': 55, 'by': 56, 'chancellor': 57, 'failure': 58, 'announce': 59, 'any': 60, 'new': 61, 'measures': 62, 'his': 63, 'Mansion': 64, 'House': 65, 'speech': 66, 'last': 67, 'Thursday': 68, 'This': 69, 'increased': 70, 'risk': 71, 'government': 72, 'being': 73, 'forced':

## Run the default solution on dev

In [3]:
chunker = LSTMTagger(os.path.join('../data', 'train.txt.gz'), os.path.join('../data', 'chunker'), '.tar')
decoder_output = chunker.decode('../data/input/dev.txt')

100%|██████████| 1027/1027 [00:01<00:00, 936.27it/s]


## Evaluate the default output

In [5]:
flat_output = [ output for sent in decoder_output for output in sent ]
import conlleval
true_seqs = []
with open(os.path.join('data','reference','dev.out')) as r:
    for sent in conlleval.read_file(r):
        true_seqs += sent.split()
conlleval.evaluate(true_seqs, flat_output)

processed 23663 tokens with 11896 phrases; found: 11672 phrases; correct: 8568.
accuracy:  84.35%; (non-O)
accuracy:  85.65%; precision:  73.41%; recall:  72.02%; FB1:  72.71
             ADJP: precision:  36.49%; recall:  11.95%; FB1:  18.00  74
             ADVP: precision:  71.36%; recall:  39.45%; FB1:  50.81  220
            CONJP: precision:   0.00%; recall:   0.00%; FB1:   0.00  0
             INTJ: precision:   0.00%; recall:   0.00%; FB1:   0.00  0
               NP: precision:  70.33%; recall:  76.80%; FB1:  73.42  6811
               PP: precision:  92.40%; recall:  87.14%; FB1:  89.69  2302
              PRT: precision:  65.00%; recall:  57.78%; FB1:  61.18  40
             SBAR: precision:  84.62%; recall:  41.77%; FB1:  55.93  117
               VP: precision:  63.66%; recall:  58.25%; FB1:  60.83  2108


(73.40644276901988, 72.02420981842637, 72.70875763747455)

## Check torch.nn.embedding
- randomly generate words embedding (by running cells below several times)

In [5]:
word_to_ix = {"hello": 0, "pikachi": 1, "world": 2}
embeds = nn.Embedding(len(word_to_ix), 5)  # 2 words in vocab, 5 dimensional embeddings

lookup_tensor = torch.tensor([word_to_ix["hello"]], dtype=torch.long)
hello_embed = embeds(lookup_tensor)

lookup_tensor = torch.tensor([word_to_ix["world"]], dtype=torch.long)
world_embed = embeds(lookup_tensor)

lookup_tensor = torch.tensor([word_to_ix["pikachi"]], dtype=torch.long)
pikachi_embed = embeds(lookup_tensor)

print('hello embedding:', hello_embed)
print('world embedding:', world_embed)
print('pikachi embedding:', pikachi_embed)

cos = nn.CosineSimilarity(dim=1, eps=1e-6)
print(cos(hello_embed, world_embed))
print(cos(pikachi_embed, world_embed))
print(cos(pikachi_embed, hello_embed))

hello embedding: tensor([[ 0.2673, -0.4212, -0.5107, -1.5727, -0.1232]], grad_fn=<EmbeddingBackward>)
world embedding: tensor([[-0.4791,  1.3790,  2.5286,  0.4107, -0.9880]], grad_fn=<EmbeddingBackward>)
pikachi embedding: tensor([[ 3.5870, -1.8313,  1.5987, -1.2770,  0.3255]], grad_fn=<EmbeddingBackward>)
tensor([-0.4688], grad_fn=<DivBackward1>)
tensor([-0.0744], grad_fn=<DivBackward1>)
tensor([0.3675], grad_fn=<DivBackward1>)


## Documentation

Write some beautiful documentation of your program here.

## Analysis

Do some analysis of the results. What ideas did you try? What worked and what did not?